In [175]:
# imports
import folium
from haversine import haversine, Unit
from pprint import pprint
import numpy as np
import time as t
import pandas as pd
from datetime import datetime, timedelta
from decimal import Decimal, ROUND_UP
import osmnx as ox
import networkx as nx
import sys
import io
from PIL import Image
import folium.plugins as plugins
from IPython.display import display, clear_output

np.set_printoptions(threshold=sys.maxsize)

ox.config(log_console=False, use_cache=True)

In [110]:
# Khi - HQ
Khi_latlng = (24.853803, 67.035395)

# Saleh Pat
slp_latlng = (27.519, 69.044)

# Hyd - Cantt
hyd_latlang = (25.399066, 68.359492)

# Bdn - Cantt
bdn_latlang = (24.657308, 68.859181)


In [3]:
# location where you want to find your route
place     = 'Sindh, Pakistan'
# find shortest route based on the mode of travel
mode      = 'drive'        # 'drive', 'bike', 'walk'
# find shortest path based on distance or time
optimizer = 'length'        # 'length','time'

# Get all nodes in a certain area which are permissible for driving
graph = ox.graph_from_place(place, network_type = mode, simplify = False)

C:\ProgramData\Anaconda3\envs\ox\lib\site-packages\osmnx\geocoder.py:110: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  gdf = gdf.append(_geocode_query_to_gdf(q, wr, by_osmid))


In [111]:
def init_folium_map():
    
    basic_map = folium.Map(location= (26.277998, 68.288195), 
                           zoom_start=7, 
                           control_scale= True)
    
    folium.TileLayer('Stamen Terrain').add_to(basic_map)
    folium.TileLayer('Stamen Toner').add_to(basic_map)
    folium.TileLayer('Stamen Water Color').add_to(basic_map)
    folium.TileLayer('cartodbpositron').add_to(basic_map)
    folium.TileLayer('cartodbdark_matter').add_to(basic_map)
    
    
    
    return basic_map

In [155]:
def zoom_path(path_list):
    
    interpol_path_list = []
    
    for i in range(len(path_list)-1):
        
        # Interpolation of orignal point from line formula
        # increase np.linspace value for refinement
        
        # since end point will be catered for in the next iteration, endpoint = False
        # x = x1 + (x2-x1) * t
        # y = y1 + (y2-y1) * t
        
        for t in np.linspace(0, 1, 20, endpoint= False ):
        
            interpol_val_x = path_list[i][0] + (path_list[i+1][0] - path_list[i][0]) * t
            interpol_val_y = path_list[i][1] + (path_list[i+1][1] - path_list[i][1]) * t
            interpol_val = (interpol_val_x, interpol_val_y)
            interpol_path_list.append(interpol_val)
    
    return interpol_path_list

In [156]:
def get_path_coordinates(cvy_start, cvy_dest):
    
    path_list = []
    if cvy_start == 'Karachi':
        # Khi - HQ
        start_latlng = Khi_latlng
        
        if cvy_dest == 'Hyderabad':
            end_latlng = hyd_latlang
        
        if cvy_dest == 'Badin':
            end_latlng = bdn_latlang
            
        if cvy_dest == 'Saleh Pat':
            end_latlng = slp_latlng
        
        
    if cvy_start == 'Hyderabad':
        # Khi - HQ
        start_latlng = hyd_latlang
        
        if cvy_dest == 'Karachi':
            end_latlng = Khi_latlng
        
        if cvy_dest == 'Badin':
            end_latlng = bdn_latlang
            
        if cvy_dest == 'Saleh Pat':
            end_latlng = slp_latlng
            
    if cvy_start == 'Badin':
        # Khi - HQ
        start_latlng = bdn_latlang
        
        if cvy_dest == 'Hyderabad':
            end_latlng = hyd_latlang
        
        if cvy_dest == 'Karachi':
            end_latlng = Khi_latlng
            
        if cvy_dest == 'Saleh Pat':
            end_latlng = slp_latlng
        
    if cvy_start == 'Saleh Pat':
        # Khi - HQ
        start_latlng = slp_latlng
        
        if cvy_dest == 'Hyderabad':
            end_latlng = hyd_latlang
        
        if cvy_dest == 'Badin':
            end_latlng = bdn_latlang
            
        if cvy_dest == 'Karachi':
            end_latlng = Khi_latlng

    
    # find the nearest node to the start location
    orig_node = ox.get_nearest_node(graph, start_latlng)

    # find the nearest node to the end location
    dest_node = ox.get_nearest_node(graph, end_latlng)
    
    #  find the shortest path
    shortest_route = nx.shortest_path(graph,
                                      orig_node,
                                      dest_node,
                                      weight=optimizer)
    
    for shortlisted_node in shortest_route:
        path_list.append((graph.nodes[shortlisted_node]["y"], 
                          graph.nodes[shortlisted_node]["x"]))
    
    interpol_path_list = zoom_path(path_list)
    
    return interpol_path_list

In [157]:
def get_input_distance(start_time, user_time, speed):
        
    t1 = datetime.strptime(str(start_time)[0:2] + ':' + str(start_time)[2:4], '%H:%M')
    t2 = datetime.strptime(str(user_time)[0:2] + ':' + str(user_time)[2:4], '%H:%M')
    
    if t2 > t1:
        td = t2 - t1
        time_spent = td.total_seconds()/3600
    else:
        time_spent = 0

    dist_now = speed*time_spent
        
    return dist_now


In [158]:
def get_dist_coordinates(coordinates):
    
    cumulative_dist = 0
    dist_list = []
    
    for index in range(len(coordinates)):
        if index:
            dist_one = haversine(coordinates[index-1], coordinates[index])
            cumulative_dist += dist_one
            dist_list.append(cumulative_dist)
        else:
            dist_one = 0
            dist_list.append(dist_one)
    
    return dist_list


In [159]:
def get_relative_distance(user_distance, dist_coordinates):
    
    relative_dist = []

    for dist in dist_coordinates:
        
        temp = abs(dist - user_distance)
        relative_dist.append(temp)
        
    return relative_dist

In [160]:
def create_path(path, cvy_color, folium_map):
# expects a list of tuples containing path coordinates ... [(1,1),(2,2),(3,3)...]
    
    folium.PolyLine(path,
                color= cvy_color,
                weight=3,
                opacity=0.7).add_to(folium_map)

In [161]:
def draw_point_circle(x1y1, x2y2, circle_color):
    
    
    
    x1 = x1y1[0]
    y1 = x1y1[1]
    
    x2 = x2y2[0]
    y2 = x2y2[1]
    
    
    diameter = haversine(x1y1, x2y2)*1000
    radius = (diameter / 2)
    
    xC, yC = (x1 + x2) / 2.0, (y1 + y2) / 2.0
    
    folium.Circle(location= (xC, yC), 
                  radius= radius,
                  color= 'yellow',
                  fill_color= circle_color).add_to(fg_circles)
    
#     folium.LayerControl().add_to(basic_map)

In [177]:
"""Read data from excel file"""

cvy_inputs_df = pd.read_excel('Inputs.xlsx', sheet_name= 'Sheet1',header= 0, converters= {'Veh Count': int,
                                                                                          'Name': str,
                                                                                          'Start': str,
                                                                                          'Destination': str,
                                                                                          'Start Time': str,
                                                                                          'Color': str,
                                                                                          'Speed': int, 
                                                                                          'Spacing': int})

start_time = cvy_inputs_df['Start Time'].min()

cvy_inputs_df = cvy_inputs_df.reindex(cvy_inputs_df.columns.tolist() + ['Coordinates',
                                                                        'Distance',
                                                                        'Relative Distance',
                                                                        'Vehicle Coordinates'], axis=1)

cvy_inputs_df['Coordinates'] = 0
cvy_inputs_df['Distance'] = 0
cvy_inputs_df['Relative Distance'] = 0
cvy_inputs_df['Vehicle Coordinates'] = 0


cvy_inputs_df['Coordinates'] = cvy_inputs_df['Coordinates'].astype('object')
cvy_inputs_df['Distance'] = cvy_inputs_df['Distance'].astype('object')
cvy_inputs_df['Relative Distance'] = cvy_inputs_df['Relative Distance'].astype('object')
cvy_inputs_df['Vehicle Coordinates'] = cvy_inputs_df['Relative Distance'].astype('object')
    
cvy_inputs_df

Veh Count       Name      Start Destination Start Time  Color  Speed  \
0         80      37 FF    Karachi   Hyderabad       0800    red     50   
1         80  63 Baloch  Hyderabad   Saleh Pat       0800  black     50   
2         80  22 Punjab    Karachi   Saleh Pat       0900    red     50   
3         80      47 AK  Hyderabad       Badin       0900  black     50   

   Spacing Coordinates Distance Relative Distance Vehicle Coordinates  
0      200           0        0                 0                   0  
1      200           0        0                 0                   0  
2      200           0        0                 0                   0  
3      200           0        0                 0                   0

In [178]:
for index, rows in cvy_inputs_df.iterrows():
    
    # get coordinates based on route and append to dataframe as new column 'Coordinates'
    path = get_path_coordinates(rows['Start'], rows['Destination'])
    cvy_inputs_df.at[index, 'Coordinates'] = path

C:\ProgramData\Anaconda3\envs\ox\lib\site-packages\osmnx\distance.py:356: UserWarning: The `get_nearest_node` function has been deprecated and will be removed in a future release. Use the more efficient `distance.nearest_nodes` instead.
  warnings.warn(msg)
C:\ProgramData\Anaconda3\envs\ox\lib\site-packages\osmnx\distance.py:356: UserWarning: The `get_nearest_node` function has been deprecated and will be removed in a future release. Use the more efficient `distance.nearest_nodes` instead.
  warnings.warn(msg)
C:\ProgramData\Anaconda3\envs\ox\lib\site-packages\osmnx\distance.py:356: UserWarning: The `get_nearest_node` function has been deprecated and will be removed in a future release. Use the more efficient `distance.nearest_nodes` instead.
  warnings.warn(msg)
C:\ProgramData\Anaconda3\envs\ox\lib\site-packages\osmnx\distance.py:356: UserWarning: The `get_nearest_node` function has been deprecated and will be removed in a future release. Use the more efficient `distance.nearest_nodes

In [183]:
dt = datetime.strptime('26 Sep 2012', '%d %b %Y')
time_list =[]
for hr in range(8, 24):
    for mn in range(0, 60, 30):
        newdatetime = dt.replace(hour=hr, minute=mn)
        time_list.append(newdatetime)

time_list_str = []
for tdate in time_list:
    time_list_str.append("{:02d}{:02d}".format(tdate.hour, tdate.minute))
    
print(time_list_str)

['0800', '0830', '0900', '0930', '1000', '1030', '1100', '1130', '1200', '1230', '1300', '1330', '1400', '1430', '1500', '1530', '1600', '1630', '1700', '1730', '1800', '1830', '1900', '1930', '2000', '2030', '2100', '2130', '2200', '2230', '2300', '2330']


In [184]:
exit_case = 0
t = 0

while exit_case != -1:
    
    exit_case = int(input('Next: 1, Back: 0, Exit: -1'))
    
    clear_output(wait= False)
    
    if exit_case == -1:
        break
    
    if exit_case == 1:
        t+=1
    
    if exit_case == 0:
        t-=1
    
    user_time = time_list_str[t]
    
    print(user_time)
    
    basic_map = init_folium_map()
    fg_circles = folium.FeatureGroup(name= 'circleLayer', overlay= True)


    # get distances based on coordinates and append to dataframe as new column 'Distance'
    for index, rows in cvy_inputs_df.iterrows():

        dist_temp = get_dist_coordinates(rows['Coordinates'])
        cvy_inputs_df.at[index, 'Distance'] = dist_temp

    for index, rows in cvy_inputs_df.iterrows():

        # converts time into distance travelled along a path
        current_dist = get_input_distance(rows['Start Time'], user_time, rows['Speed'])
        cvy_inputs_df.at[index, 'Current Head Distance'] = current_dist


    # find shortest distance of user_distance - rows['Distance']
    for index, rows in cvy_inputs_df.iterrows():

        relative_dist = get_relative_distance(rows['Current Head Distance'], rows['Distance'])
        cvy_inputs_df.at[index, 'Relative Distance'] = relative_dist

        create_path(rows['Coordinates'], rows['Color'], basic_map)

    for index, rows in cvy_inputs_df.iterrows():
        # safety check - ensure convoy has started its journey
        if rows['Current Head Distance'] != 0:
            # repeat process for every vehicle in convoy
            vehicle_index_min = []

            for vehicle_num in range(rows['Veh Count']):

                if vehicle_num == 0:
                    # first vehicle, will always be relative distance = 0
                    index_min = np.argmin(rows['Relative Distance'])
                    # mark index for vehicle
                    vehicle_index_min.append(index_min)
                    zero_val = rows['Distance'][index_min] 
                else:
                    # iterate backwards for the rest of vehicles from zero_val of distance
                    j = 0
                    while 1:
                        # safety check - ensure we do not iterate below 0, incase vehicles are too many and
                        # coordinates are not enough from given location

                        if index_min - j >= 0:
                            # when current index has a distance greater than spacing required for nth vehicle
                            if abs(zero_val - rows['Distance'][index_min-j]) > (rows['Spacing']*vehicle_num)/1000:
                                index_min = index_min - j
                                # mark index for vehicle
                                vehicle_index_min.append(index_min)
                                break
                        else:
                            break
                        j+=1

                    cvy_inputs_df.at[index, 'Vehicle Coordinates']= vehicle_index_min

            # first and last vehicle coordinates, two points to determine radius of circle
            draw_point_circle(rows['Coordinates'][vehicle_index_min[0]],
                              rows['Coordinates'][vehicle_index_min[len(vehicle_index_min) - 1]],
                              rows['Color'])


            for index, index_min in enumerate(vehicle_index_min):

                coordinates_min = rows['Coordinates'][index_min]

                popup_text = str(rows['Name']) + ' Distance Travelled: ' + str(round(rows['Distance'][index_min], 2)) + " KM"

                if index == 0 or index == (rows['Veh Count'] - 1):

                    folium.Marker(location= coordinates_min, 
                                  popup= popup_text,
                                  icon= folium.Icon(color=rows['Color'], 
                                                    icon_color='white', 
                                                    icon = 'fa-truck', 
                                                    prefix='fa')
                                 ).add_to(basic_map)
                else:

                    folium.CircleMarker(location= coordinates_min,
                                        radius= 3,
                                        color= 'yellow',
                                        fill= True,
                                        fill_opacity= 1).add_child(folium.Popup(popup_text)).add_to(basic_map)

        else:

            popup_text = str(rows['Name']) + ' Distance Travelled: ' + str(round(rows['Distance'][index*4], 2)) + " KM"

            folium.Marker(location= rows['Coordinates'][index*4], 
                          popup= popup_text,
                          icon= folium.Icon(color=rows['Color'], 
                                            icon_color='white', 
                                            icon = 'fa-truck', 
                                            prefix='fa')).add_to(basic_map)


    fg_circles.add_to(basic_map)
    plugins.Fullscreen().add_to(basic_map)
    draw = plugins.Draw(export=False)
    draw.add_to(basic_map)
    folium.LayerControl().add_to(basic_map)
#     print('map should come')
    display(basic_map)

1630


KeyboardInterrupt: Interrupted by user